# Imports

In [ ]:
# Dependencies:
#
# Ripser: Ripser.py is a lean persistent homology package for Python.
#         https://ripser.scikit-tda.org/en/latest/
#
# persim: The PersistentImages_Chemistry repository contains tools to create persistence images (PI) 
#         that encode geometric data of chemical structures for use in machine learning applications
#         https://maroulaslab.github.io/PersistentImages_Chemistry/index.html

from ripser import Rips
from persim import PersImage
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import os
import glob
from sklearn.model_selection import KFold, train_test_split
from sklearn.ensemble import RandomForestRegressor
from dscribe.descriptors import SOAP
from ase.io import read

# Define Persistence images and SOAPs Combined Descriptor

In [ ]:
# Directory location containing XYZ files
xyz_directory = "PATHWAY" # Insert local pathway to directory containing xyz files  

# Get a list of all XYZ files in the directory
xyz_files = [os.path.join(xyz_directory, file) for file in os.listdir(xyz_directory) if file.endswith(".xyz")]

# Define SOAP parameters
species = ["H", "C", "N", "O", "F"]  # Additional elements can be included if needed
soap_descriptor = SOAP(species=species, r_cut=4.0, n_max=6, l_max=4, sparse=False)

# Define persistence images (PI) hyperparameters
pixelx = 100
pixely = 100
myspread = 0.009
myspecs = {"maxBD": 2.5, "minBD": -0.1}

# Initialize lists to store the combined descriptors
X_list = []

# Iterate over xyz files
for idx, xyz_file in enumerate(xyz_files):
    # xyz file read using ASE
    structure = read(xyz_file)
    
    # Calculation of the SOAP descriptor for the entire structure
    soap_vector = soap_descriptor.create(structure).flatten()
    
    # Prepare coordinates for PI
    coordinates = structure.get_positions()
    dummy = np.array(coordinates)
    
    # Calculation of the Persistence Diagram (Rips)
    rips = Rips(maxdim=2)
    diagrams = rips.fit_transform(dummy)
    
    # Generate Persistence Image (PI)
    pim = PersImage(pixels=[pixelx, pixely], spread=myspread, specs=myspecs, verbose=False)
    pi_vector = pim.transform(np.vstack([diagrams[0][0:-1], diagrams[1], diagrams[2]])).flatten()
    
    # Combine SOAP and PI vectors
    combined_vector = np.concatenate((soap_vector, pi_vector))
    
    # Append to X_list
    X_list.append(combined_vector)

# Find the maximum length of the combined vectors and pad the others
max_length = max(len(v) for v in X_list)
X = np.array([np.pad(v, (0, max_length - len(v)), 'constant') for v in X_list])

# X contains the combined SOAP and PI descriptors for machine learning
print(X.shape)

# Define energies corresponding to X as variable y

In [ ]:
# Read the CSV file
csv_file_path = "PATHWAY/NAME.csv"  # Replace with the actual path to your CSV file that contains a list of the xyz file names and their corresponding logB values
df = pd.read_csv(csv_file_path)

# Acquires the list of XYZ files in the "Molecules" directory for organizational purposes
molecules_directory = "PATHWAY"  # Replace with the actual path to your "Molecules" directory
xyz_files = [file for file in os.listdir(molecules_directory) if file.endswith(".xyz")]

# Filter the DataFrame to include only the rows where XYZ file names are present in the list of XYZ files to ensure matching
filtered_df = df[df['COLUMN NAME'].isin(xyz_files)] # Replace COLUMN NAME with actual name of the column containng xyz file names

# Reindex the DataFrame to match the order of XYZ files obtained from the directory
ordered_df = filtered_df.set_index('COLUMN NAME').reindex(xyz_files).reset_index() # Replace COLUMN NAME with actual name of the column containng xyz file names

# Print the ordered DataFrame
print(ordered_df)

# Extract the "logB" column values from the ordered DataFrame
y = ordered_df['COLUMN NAME with logB Values'].values # Replace "COLUMN NAME with logB Values" with the name of the column in the .csv file containing the logB values for their respective xyz file

# Print the energy values
print(y)

# Random Forest Regression Cross Validation Algorithm

In [ ]:
plt.rc('text', usetex=False)

def test_learner(X, y, model):
    kf = KFold(n_splits=5, random_state=0, shuffle=True)
    kf.get_n_splits(X)

    errorlist = []
    mdscr_list = []
    r2_train_list = []  # List to store R-squared values of the training set across folds
    r2_test_list = []   # List to store R-squared values of the testing set across folds

    for fold, (train_index, test_index) in enumerate(kf.split(X), 1):
        X_train, X_test = X[train_index], X[test_index]
        y_train, y_test = y[train_index], y[test_index]

        # Flatten the matrices to make them 2D arrays
        X_train_flat = np.array([matrix.flatten() for matrix in X_train])
        X_test_flat = np.array([matrix.flatten() for matrix in X_test])

        # Train the model on the entire training set
        model.fit(X_train_flat, y_train)

        # Calculate error on the entire testing set
        error = rmse(model.predict(X_test_flat), y_test)
        errorlist.append(error)

        # Calculate scores and errors for training set
        tr = model.score(X_train_flat, y_train)
        te = model.score(X_test_flat, y_test)

        # Store R-squared values for training and testing sets
        r2_train_list.append(tr)
        r2_test_list.append(te)

        # Print metrics for each fold
        print('Fold error {} for fold {}'.format(error, fold))
        print(tr, 'is the score for the training set')
        print(te, 'is the score for the testing set')
        print("Size of Training Set:", len(y_train))
        print("Size of Testing Set:", len(y_test))
        print()

        # Plotting for each fold
        plt.scatter(y_train.flatten(), model.predict(X_train_flat), color="b", label='Training Set')
        plt.scatter(y_test.flatten(), model.predict(X_test_flat), color="r", label='Testing Set')
        # Plot the diagonal line
        plt.plot([min(y_test.flatten()), max(y_test.flatten())], [min(y_test.flatten()), max(y_test.flatten())], '--', color='rebeccapurple')
        plt.legend(fontsize=12, loc="lower right")
        plt.ylabel('Predicted logB Interaction Energy', fontsize=12)
        plt.xlabel('DFT logB Interaction Energy', fontsize=12)
        plt.show()

        # Calculate R-squared score for the current fold
        fold_mdscr = (tr + te) / 2
        mdscr_list.append(fold_mdscr)

    # Print averages across all folds
    print('Final error {} +- {} '.format(np.average(errorlist), np.std(errorlist)))
    
    # Overall model score
    mdscr = np.mean(mdscr_list)
    print(mdscr, "is the score for the model")

    # Print mean of R-squared scores from each fold
    mean_mdscr = np.mean(mdscr_list)
    print(mean_mdscr, "is the mean of R-squared scores from each fold")

    # Print average R-squared values of training and testing sets across all folds
    avg_r2_train = np.mean(r2_train_list)
    avg_r2_test = np.mean(r2_test_list)
    print("Average R-squared on Training Set (across all folds):", avg_r2_train)
    print("Average R-squared on Testing Set (across all folds):", avg_r2_test)


def rmse(predictions, targets):
    return np.sqrt(((predictions - targets) ** 2).mean())

model = RandomForestRegressor(n_estimators = 200, criterion = 'mae', min_samples_split = 6, min_samples_leaf=6)
test_learner(X, np.array(y), model)

# Making Predictions on Unexplored XYZ Files

In [ ]:
# Directory containing XYZ files for validation
xyz_directory = "PATHWAY"  # Replace with the path to the directory containing the xyz files for prediction using the trained machine learning algorithm
xyz_files = [os.path.join(xyz_directory, file) for file in os.listdir(xyz_directory) if file.endswith(".xyz")]

# Define SOAP parameters
species = ["H", "C", "N", "O", "F"]  # Add other elements if needed
soap_descriptor = SOAP(species=species, r_cut=4.0, n_max=6, l_max=4, sparse=False)

# Define PI hyperparameters
pixelx = 100
pixely = 100
myspread = 0.009
myspecs = {"maxBD": 2.5, "minBD": -0.1}

# Initialize lists to store the combined descriptors
X_list = []

# Initialize a dictionary to store filename and predicted energy pairs
filename_energy_dict = {}

# Iterate over files
for idx, xyz_file in enumerate(xyz_files):
    # Read the xyz file using ASE
    structure = read(xyz_file)

    # Calculate the SOAP descriptor for the entire structure
    soap_vector = soap_descriptor.create(structure).flatten()

    # Prepare coordinates for PI
    coordinates = structure.get_positions()
    dummy = np.array(coordinates)

    # Calculate the Persistence Diagram (Rips)
    rips = Rips(maxdim=2)
    diagrams = rips.fit_transform(dummy)

    # Generate Persistence Image (PI)
    pim = PersImage(pixels=[pixelx, pixely], spread=myspread, specs=myspecs, verbose=False)
    pi_vector = pim.transform(np.vstack([diagrams[0][0:-1], diagrams[1], diagrams[2]])).flatten()

    # Combine SOAP and PI vectors
    combined_vector = np.concatenate((soap_vector, pi_vector))

    # Ensure the feature vector matches the expected input size
    expected_feature_length = model.n_features_in_
    if len(combined_vector) < expected_feature_length:
        combined_vector = np.pad(combined_vector, (0, expected_feature_length - len(combined_vector)), 'constant')
    elif len(combined_vector) > expected_feature_length:
        combined_vector = combined_vector[:expected_feature_length]

    # Append to X_list (for further analysis if needed)
    X_list.append(combined_vector)

    # Extract XYZ file name
    xyz_file_name = os.path.basename(xyz_file)
        
    # Prediction (replace this with your actual model prediction)
    predicted_energy = model.predict(combined_vector.reshape(1, -1))[0]
    
    # Store filename and predicted energy in the dictionary
    filename_energy_dict[xyz_file_name] = predicted_energy

# Sort the dictionary by predicted energy values
sorted_filename_energy = sorted(filename_energy_dict.items(), key=lambda x: x[1])

# Reverse the sorted list
sorted_filename_energy.reverse()

# Print the top n predicted values 
print("\nTop n Predicted Values:")
for filename, energy in sorted_filename_energy[:n]: # Change "n" with a numerical value
    print(f"Filename: {filename}, Predicted Energy: {energy}")